# Sephora Customer Insights
Welcome to our exploration of Sephora's product and customer data! This notebook uncovers what customers love, how they rate products, and what drives their decisions. Today we will try to understanding Sephora's product performance and customer sentiment.
The dashboards will address:
- **Product Popularity and Engagement**: Which products and brands drive the most customer love?

- **Customer Satisfaction Trends**: How do ratings and recommendations vary across categories?

- **Price vs. Quality** Analysis: Is there a correlation between price and customer satisfaction?

- **Review Helpfulness Insights**: What makes a review helpful to customers?



In [13]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode
init_notebook_mode(connected=True)
from ipywidgets import interact, widgets
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

pd.options.display.max_rows = 30
pd.options.display.max_columns = 25

df = pd.read_csv("/Users/leilaossena/Desktop/codeop/module1/personal_project/sephora-data-portfolio/sephora_final_clean_dataset.csv")


## Product Popularity and Engagement
 The objective here is to Highlight top-performing products and brands based on customer engagement (loves_count) and review activity (reviews)

In [14]:
@interact(brand=widgets.Dropdown(options=["All"] + list(df['brand_name'].unique()), description="Brand"))
def plot_popularity(brand):
    if brand != "All":
        filtered_df = df[df['brand_name'] == brand]
    else:
        filtered_df = df
    
    
    product_summary = filtered_df.groupby('product_name').agg({
        'loves_count': 'sum',
        'reviews': 'sum',
        'product_rating': 'mean'
    }).reset_index().sort_values('loves_count', ascending=False).head(10)
    
   
    fig = px.bar(
        product_summary,
        x='product_name',
        y='loves_count',
        color='product_rating',
        hover_data=['reviews'],
        title=f"Top 10 Products by Loves Count ({brand})",
        labels={'loves_count': 'Loves Count', 'product_name': 'Product', 'product_rating': 'Average Rating'}
    )
    fig.update_layout(xaxis_tickangle=45, showlegend=True)
    fig.show()

interactive(children=(Dropdown(description='Brand', options=('All', 'NUDESTIX', 'LANEIGE', 'The INKEY List', '…

## Customer Satisfaction Trends
We want to analyse Analyze customer satisfaction (review_rating and is_recommended) across product categories.

In [15]:
@interact(category=widgets.Dropdown(options=["All"] + list(df['primary_category'].unique()), description="Category"))
def plot_satisfaction(category):
    if category != "All":
        filtered_df = df[df['primary_category'] == category]
    else:
        filtered_df = df
    
   
    category_summary = filtered_df.groupby('secondary_category').agg({
        'review_rating': 'mean',
        'is_recommended': 'mean',
        'product_id': 'count'
    }).reset_index().rename(columns={'product_id': 'product_count'})
    
    
    fig = px.scatter(
        category_summary,
        x='review_rating',
        y='is_recommended',
        size='product_count',
        color='secondary_category',
        hover_data=['product_count'],
        title=f"Customer Satisfaction by Category ({category})",
        labels={
            'review_rating': 'Average Review Rating',
            'is_recommended': 'Recommendation Rate',
            'product_count': 'Number of Products'
        }
    )
    fig.update_layout(showlegend=True)
    fig.show()

interactive(children=(Dropdown(description='Category', options=('All', 'Skincare'), value='All'), Output()), _…

## Price vs. Quality Analysis
lets Explore the relationship between product price and customer satisfaction.



In [16]:
@interact(price_category=widgets.Dropdown(options=["All"] + list(df['price_category'].unique()), description="Price Category"))
def plot_price_quality(price_category):
    if price_category != "All":
        filtered_df = df[df['price_category'] == price_category]
    else:
        filtered_df = df
    
    fig = px.scatter(
        filtered_df,
        x='price_usd',
        y='product_rating',
        color='primary_category',
        size='reviews',
        hover_data=['product_name', 'brand_name'],
        title=f"Price vs. Rating by Product ({price_category})",
        labels={'price_usd': 'Price (USD)', 'product_rating': 'Average Rating', 'reviews': 'Review Count'}
    )
    fig.update_layout(showlegend=True)
    fig.show()

interactive(children=(Dropdown(description='Price Category', options=('All', 'Low', 'High', 'Medium', 'Luxury'…

## Review Helpfulness Insights
We will identify what makes a review helpful to customers.




In [17]:
@interact(category=widgets.Dropdown(options=["All"] + list(df['primary_category'].unique()), description="Category"))
def plot_helpfulness(category):
    if category != "All":
        filtered_df = df[df['primary_category'] == category]
    else:
        filtered_df = df
    
    helpfulness_summary = filtered_df.groupby('review_rating').agg({
        'helpfulness': 'mean',
        'review_text': 'count'
    }).reset_index().rename(columns={'review_text': 'review_count'})
   
    fig = go.Figure()
    fig.add_trace(go.Scatter(
        x=helpfulness_summary['review_rating'],
        y=helpfulness_summary['helpfulness'],
        mode='lines+markers',
        name='Helpfulness',
        hovertemplate='Rating: %{x}<br>Helpfulness: %{y:.2f}<br>Reviews: %{customdata}',
        customdata=helpfulness_summary['review_count']
    ))
    fig.update_layout(
        title=f"Review Helpfulness by Rating ({category})",
        xaxis_title="Review Rating",
        yaxis_title="Average Helpfulness Score",
        showlegend=True
    )
    fig.show()

interactive(children=(Dropdown(description='Category', options=('All', 'Skincare'), value='All'), Output()), _…